# Notebook: Quick accessibility analysis using H3pandas

Chingiz Zhanarbaev, 02.2024

This notebook demonstrates use-case of [NxTransit](https://github.com/chingiztob/Transit). In this notebook, we will use the library to calculate mean travel time for different parts of Chelyabinsk, Russia using [H3 hexagons](https://uber.github.io/h3-py/intro.html).

In [1]:
import pandas as pd
import osmnx as ox
import folium
import geopandas as gpd
import h3pandas

import nxtransit as nt

## Initialize data

The first step is to initialize a graph object. Transit graph is a `DiGraph` object and contains spetial attributes for handling dynamic nature of GTFS data.

In [2]:
# Setting up the parameters

GTFSpath = r"Feeds\Chelyabinsk" # Path to the folder with GTFS files
departure_time_input = "6:00:00" # # Departure time in HH:MM:SS format
day = 'monday' # # Day of the week

In [3]:
nt.validate_feed(GTFSpath)

GTFS feed is valid.


True

In [4]:
%%capture
transit_graph, stops = nt.feed_to_graph(GTFSpath = GTFSpath, day_of_week = day, departure_time_input = departure_time_input,
                                        duration_seconds=3600*18, read_shapes=False, multiprocessing=True, load_graphml=True,
                                        input_graph_path=r"D:\Python_progs\Output\Chelyabinsk_graph.graphml")

### Prepare buildings geodataframe using OSMnx

In [5]:
tags = {"building": True}
buildings = ox.features_from_place("Chelyabinsk", tags)
building_centroids = gpd.GeoDataFrame(buildings, geometry=buildings.geometry.centroid)

### Aggregate OSM buildings with H3 hexagons using `h3pandas`

Resulting geodataframe will contain only hexagons that have buildings in them.

In [7]:
building_centroids_h3 = building_centroids.h3.geo_to_h3_aggregate(9, return_geometry=True)

In [8]:
building_centroids_h3.explore()

## Calculate OD-cost matrix

### Snap H3 centroids to network

Add `id` field to the polygons, which will be used as a node id in the graph

In [ ]:
building_centroids_h3['id'] = building_centroids_h3.index
hex_centroids = nt.create_centroids_dataframe(building_centroids_h3)
nt.snap_points_to_network(transit_graph, hex_centroids)

### Perform OD-cost matrix calculation

In [18]:
# Create list of nodes for OD calculation
nodes = list(hex_centroids['origin_id'])
od_matrix = nt.calculate_od_matrix_parallel(transit_graph, nodes,  3600*18, 6)

Calculating the OD using 6 processes
Graph size 236.16 MB, expected costs 4.61 GB, memory avaliable 6.16 GB
Time elapsed: 543.1553788999954


Group OD-cost matrix by source node and calculate the average travel time to all other nodes

In [19]:
od_group = od_matrix.groupby('source_node')['travel_time'].mean().reset_index()

Merge data from OD-cost matrix with the H3 geodataframe

In [20]:
df = pd.merge(building_centroids_h3, od_group, left_on='id', right_on='source_node')

## Plot results using folium

In [29]:
frame_center_lat = stops['stop_lat'].mean()
frame_center_lon = stops['stop_lon'].mean()

map = folium.Map(location=[frame_center_lat, frame_center_lon], 
                zoom_start=11,
                width='100%', height='100%')

df.explore(m = map,
            column = 'travel_time',
            cmap = 'RdYlGn_r',
            legend=True,
            tooltip = 'travel_time',
            legend_kwds=dict(colorbar=False),
            scheme='Quantiles', k=6)